In [2]:
# IP USED THROUGHOUT THE ASSIGNMENT
hostip = "172.22.32.1"

In [3]:
import sys
import os
import threading
import time
import json
from kafka3 import KafkaProducer, KafkaConsumer
from datetime import datetime as dt
from pymongo import MongoClient
from pyspark.sql import Row
import pandas as pd
import os
# add the folder where util.py lives
#sys.path.append(os.path.join(os.getcwd(), 'fit3182-a2'))
from util import kafkaProducer

In [4]:
from kafka3.admin import KafkaAdminClient, NewTopic
import time
def recreate_topics(bootstrap_servers:str, topics:str,
                    num_partitions:int=1, replication_factor:int=1):
    """
    This function are created to help purge Kafka producer streams we just created to
    
    """
    # Ensure we pass a list of host:port strings
    if isinstance(bootstrap_servers, str):
        bs_list = [bootstrap_servers]
    else:
        bs_list = bootstrap_servers

    admin = KafkaAdminClient(bootstrap_servers=bs_list)
    try:
        admin.delete_topics(topics)
        print(f"[INFO] Deletion of topics {topics} initiated.")
    except Exception as e:
        print(f"[WARN] Could not delete topics: {e}")

    time.sleep(2)

    new_topics = [
        NewTopic(name=t, num_partitions=num_partitions, replication_factor=replication_factor)
        for t in topics
    ]
    try:
        admin.create_topics(new_topics)
        print(f"[INFO] Recreated topics {topics}.")
    except Exception as e:
        print(f"[ERROR] Failed to create topics {topics}: {e}")
        raise
    finally:
        admin.close()


In [ ]:
#List out all the csv dataset of camera A, B, and C
csv_path_a="data/camera_event_A.csv"
csv_path_b="data/camera_event_B.csv"
csv_path_c="data/camera_event_C.csv"

#server ip address where kafka container listen to
kafka_server=f"{hostip}:9092"

#Producers tag we included for each camera
producer_id_a="A"
producer_id_b="B"
producer_id_c="C"

batch_interval=5

#Topic to recognise each different streams
topics = ["camera_event_a", "camera_event_b", "camera_event_c"]

# PURGE & RECREATE before producing
recreate_topics(kafka_server, topics,
                num_partitions=1,
                replication_factor=1)

#Instantiating different kafka producer
producer_a = kafkaProducer(csv_path_a, kafka_server, producer_id_a, topics[0], batch_interval)
producer_b = kafkaProducer(csv_path_b, kafka_server, producer_id_b, topics[1], batch_interval)
producer_c = kafkaProducer(csv_path_c, kafka_server, producer_id_c, topics[2], batch_interval)


threads = []
#Run the threadings together through produce_batches
for p in (producer_a, producer_b, producer_c):
    t = threading.Thread(target=p.produce_batches, daemon=True)
    t.start()
    threads.append(t)

for t in threads:
    t.join()

[WARN] Could not delete topics: [Error 3] UnknownTopicOrPartitionError: Request 'DeleteTopicsRequest_v3(topics=['camera_event_a', 'camera_event_b', 'camera_event_c'], timeout=30000)' failed with response 'DeleteTopicsResponse_v3(throttle_time_ms=0, topic_error_codes=[(topic='camera_event_a', error_code=3), (topic='camera_event_b', error_code=3), (topic='camera_event_c', error_code=3)])'.
[INFO] Recreated topics ['camera_event_a', 'camera_event_b', 'camera_event_c'].
[INFO] Successfully loaded data from data/camera_event_A.csv
print 172.22.32.1:9092
[INFO] Successfully loaded data from data/camera_event_B.csv
print 172.22.32.1:9092
[INFO] Successfully loaded data from data/camera_event_C.csv
print 172.22.32.1:9092
172.22.32.1:9092
172.22.32.1:9092
172.22.32.1:9092
[INFO] Publishing batch #1 (20 records)...
[INFO] Publishing batch #1 (5 records)...
[INFO] Publishing batch #1 (1 records)...
[INFO] Batch #1 sent. Sleeping 5s...[INFO] Batch #1 sent. Sleeping 5s...

[INFO] Batch #1 sent. Sle

[INFO] Publishing batch #4 (20 records)...
[INFO] Publishing batch #4 (4 records)...
[INFO] Publishing batch #4 (2 records)...
[INFO] Batch #4 sent. Sleeping 5s...
[DATA] Batch #4:
                                event_id  batch_id car_plate  camera_id  \
60  1dd988c0-d000-489b-8cf0-2cd738fb0565         4    BQN 88          1   
61  9478323b-a2f6-4592-8c9f-a9de5bb984ab         4  ZEA 3530          1   
62  3e613964-b717-44a8-bf81-a1290ae07a35         4     SJ 15          1   
63  9f538681-69f0-4efd-a3e3-ef44ee2c1094         4     PB 55          1   
64  26e1dd39-29ec-4692-bca0-5705579ed316         4      BU 9          1   
65  865113cf-ff8a-41ea-b9f6-48a76b8dc3c4         4     WX 49          1   
66  8217c776-2542-4494-851f-c603e4adaee1         4  HLZ 1649          1   
67  f2deda9c-401b-4a0f-8d43-47c0871ff7d6         4    YY 765          1   
68  f44716e8-a218-4484-8ffc-8aca0e5c3a04         4    VLY 61          1   
69  2daa2630-7379-4d52-abc5-466ba64c3f33         4     WOQ 4         

[INFO] Publishing batch #7 (2 records)...
[INFO] Publishing batch #7 (3 records)...
[INFO] Batch #7 sent. Sleeping 5s...
[DATA] Batch #7:
                               event_id  batch_id car_plate  camera_id  \
8  cc084bd6-f680-43cf-9d6e-15bc481038b2         7  PKH 8115          3   
9  676fa9f2-4a5b-4d1b-a63e-a59b1f2e5c26         7      PI 9          3   

                   timestamp  speed_reading  
8 2024-01-01 08:08:52.583094          153.8  
9 2024-01-01 08:08:53.620450          134.3  

[INFO] Publishing batch #7 (20 records)...
[INFO] Batch #7 sent. Sleeping 5s...
[DATA] Batch #7:
                                event_id  batch_id car_plate  camera_id  \
17  7dff112a-d3ce-4ebb-841f-ea3e03662ead         7    WB 418          2   
18  1f739fcb-8e46-4c92-a69b-9a18533cb646         7      PI 9          2   
19  756a47f3-7f81-4e17-88fa-b2bbed9aa29e         7  PKH 8115          2   

                    timestamp  speed_reading  
17 2024-01-01 08:08:24.091422          138.8  
18 2024-

[INFO] Publishing batch #10 (2 records)...
[INFO] Publishing batch #10 (2 records)...
[INFO] Batch #10 sent. Sleeping 5s...
[DATA] Batch #10:
                                event_id  batch_id car_plate  camera_id  \
13  2f38e970-5042-4d91-8ef3-f8e4bed9908f        10    CZ 592          3   
14  fa9e3b2a-de4e-48be-b97b-1c01e95e437a        10      AH 8          3   

                    timestamp  speed_reading  
13 2024-01-01 08:00:47.453301          161.4  
14 2024-01-01 08:00:49.247531          165.5  

[INFO] Batch #10 sent. Sleeping 5s...
[DATA] Batch #10:
                                event_id  batch_id car_plate  camera_id  \
23  58588fd9-1fd6-4b52-929b-406731bbce2b        10  WPV 1456          2   
24  274dffed-ed69-4f56-8a2e-5c017d27adc1        10     QJ 53          2   

                    timestamp  speed_reading  
23 2024-01-01 08:08:45.845657           75.1  
24 2024-01-01 08:08:46.302895           82.8  

[INFO] Publishing batch #10 (20 records)...
[INFO] Batch #10 sent.

[INFO] Publishing batch #13 (1 records)...
[INFO] Publishing batch #13 (1 records)...
[INFO] Batch #13 sent. Sleeping 5s...
[DATA] Batch #13:
                                event_id  batch_id car_plate  camera_id  \
17  49500aa0-39b9-4dc2-8e4d-69c8519b5983        13     JEJ 6          3   

                    timestamp  speed_reading  
17 2024-01-01 08:09:06.369311          109.3  

[INFO] Batch #13 sent. Sleeping 5s...
[DATA] Batch #13:
                                event_id  batch_id car_plate  camera_id  \
27  7dba46aa-77b5-47f5-9801-d30e5ddff0d7        13     FO 32          2   

                    timestamp  speed_reading  
27 2024-01-01 08:00:39.240776           94.8  

[INFO] Publishing batch #13 (20 records)...
[INFO] Batch #13 sent. Sleeping 5s...
[DATA] Batch #13:
                                 event_id  batch_id car_plate  camera_id  \
240  2e8b5c14-1d48-484c-8b3e-9500ee86717e        13    HM 258          1   
241  2b480838-5811-4479-b618-23f9d639eb22        13   WG 9

...

[INFO] Publishing batch #1014 (20 records)...
[INFO] Batch #1014 sent. Sleeping 5s...
[DATA] Batch #1014:
                                   event_id  batch_id car_plate  camera_id  \
20260  c6f59ba8-1c45-4dd5-a14a-fee72d9b62a7      1014  UDE 1767          1   
20261  d2325d86-72b9-4cd7-89e2-58b5029b6466      1014   UFX 022          1   
20262  15cfcfa0-fb31-4f52-b782-29dd51096806      1014   ZY 9064          1   
20263  32524304-0e97-4adf-9954-78c0b113a50f      1014      JQ 1          1   
20264  edc21466-ad4b-48a9-bbf5-a07ee5200aab      1014   BOF 419          1   
20265  4dad3976-d2da-40b4-b732-80e9d33832e5      1014    XSB 51          1   
20266  9952caf0-e200-4167-ae7b-a91cdce4064a      1014     NKM 8          1   
20267  1db33f55-03d8-44c5-be17-3f9c6f9a1c9c      1014    JB 842          1   
20268  9dd9a8b1-68f3-4dda-8711-4b2a3b2f3faf      1014   SNW 203          1   
20269  1ffc6e39-15f8-4e0b-a41e-c32b4dc4ef3d      1014   OHW 372          1   
20270  08468373-fdb1-46b4-8a48-29464

[INFO] Publishing batch #1020 (6 records)...
[INFO] Batch #1020 sent. Sleeping 5s...
[DATA] Batch #1020:
                                  event_id  batch_id car_plate  camera_id  \
1367  0d4a6911-8fe3-409e-9cca-3314f3e273ce      1020  MIV 1203          3   
1368  87035e7f-71a8-444b-b0ba-ad3300799a0f      1020     OM 31          3   
1369  e533bb73-ae6b-46b7-8be8-578b9da03e3c      1020     NET 4          3   
1370  dea9151a-c5e2-4802-910c-ad7679c64a93      1020   RH 5799          3   
1371  b9630a4a-777f-4177-8b7a-b4af8d3cbb3c      1020   WWL 965          3   
1372  54728d12-9b74-4c0d-83d8-1323eab11b37      1020    YMA 93          3   

                      timestamp  speed_reading  
1367 2024-01-01 16:35:28.583671          125.3  
1368 2024-01-01 16:35:28.761784          114.8  
1369 2024-01-01 16:35:30.065300          106.3  
1370 2024-01-01 16:35:30.844983          113.5  
1371 2024-01-01 16:35:31.784424          100.5  
1372 2024-01-01 16:35:33.008512          114.6  

[INFO] Publ

[INFO] Publishing batch #1022 (3 records)...
[INFO] Batch #1022 sent. Sleeping 5s...
[DATA] Batch #1022:
                                  event_id  batch_id car_plate  camera_id  \
1920  188d193e-0f15-4c26-b897-cea621c87a05      1022    NY 667          2   
1921  e0e3eee0-9096-4783-b096-6909213f88c5      1022     RN 95          2   
1922  5957c73e-110e-4424-be00-23770ffd3aa2      1022    FS 686          2   

                      timestamp  speed_reading  
1920 2024-01-02 11:11:14.456510          156.9  
1921 2024-01-02 11:11:16.697345          156.6  
1922 2024-01-02 11:11:17.306048          145.7  

[INFO] Publishing batch #1019 (20 records)...
[INFO] Batch #1019 sent. Sleeping 5s...
[DATA] Batch #1019:
                                   event_id  batch_id car_plate  camera_id  \
20360  80cc36a9-f10d-4127-8cf5-b11a5e1dc365      1019     RA 98          1   
20361  6d122395-e6c8-4c97-9c64-bda590dda108      1019   TY 1923          1   
20362  376f8bf3-bca3-447c-9608-9820733dd51b      

[INFO] Publishing batch #1025 (5 records)...
[INFO] Batch #1025 sent. Sleeping 5s...
[DATA] Batch #1025:
                                  event_id  batch_id car_plate  camera_id  \
1384  120a3315-7eeb-4c77-9a78-fcc9248a93ef      1025   YAV 321          3   
1385  47b36090-09fc-441a-9145-72744a6de1e8      1025    ANF 57          3   
1386  9d21da37-56e3-4b7d-98c0-4633ac5c773b      1025    VL 717          3   
1387  36660474-b5ec-41bd-ac18-1ffaf4b374eb      1025     WCQ 7          3   
1388  fe73fdd7-1227-4e90-9a3f-fb5eae08dd08      1025    SJS 31          3   

                      timestamp  speed_reading  
1384 2024-01-01 16:44:52.497015          136.8  
1385 2024-01-01 16:44:52.907703          125.0  
1386 2024-01-01 16:44:52.937787          127.8  
1387 2024-01-01 16:44:53.528320          125.7  
1388 2024-01-01 16:44:56.593892          138.7  

[INFO] Publishing batch #1025 (1 records)...
[INFO] Batch #1025 sent. Sleeping 5s...
[DATA] Batch #1025:
                                

[INFO] Publishing batch #1024 (20 records)...
[INFO] Batch #1024 sent. Sleeping 5s...
[DATA] Batch #1024:
                                   event_id  batch_id car_plate  camera_id  \
20460  aa798369-738b-41ba-a869-5c52c415702d      1024   OP 2090          1   
20461  4e007065-decc-4d0c-ae58-eaa77566d47e      1024   CKU 030          1   
20462  40c63f04-0268-453e-a4bd-44001079c4e8      1024   MZB 846          1   
20463  82b1d498-40cc-41f6-b116-209ff3f78ddf      1024    JKU 05          1   
20464  2e12516c-40df-4736-8169-b5c3593f7cc4      1024   ARL 255          1   
20465  f2fa2eee-c4ca-4a8b-9401-848e51d8ecad      1024    KKM 55          1   
20466  ab30939f-0ae6-42da-b222-1cc279bdbed0      1024  BHK 0265          1   
20467  a9da9046-f253-4b83-8913-634024f95dd7      1024  ORK 8667          1   
20468  0d3af189-99e2-4151-a8d5-4fea9241c9b5      1024    YA 856          1   
20469  ebe75e9e-8be4-4445-b812-5ebb31cd7b5c      1024   PI 8823          1   
20470  8f8b73fd-b93d-4c6f-88cf-a9f4a